In [26]:
import json
from matplotlib import pyplot as plt
import xtrack as xt
import numpy as np
import plotly.graph_objects as go


In [27]:
BEAM  = "b1"

In [28]:
collider = xt.Multiline.from_json('../collider/collider_43.json')
line = collider[f'lhc{BEAM}']

Loading line from dict: 100%|██████████| 30782/30782 [00:01<00:00, 18513.09it/s]


Done loading line from dict.           


Loading line from dict: 100%|██████████| 30818/30818 [00:02<00:00, 11487.01it/s]


Done loading line from dict.           


Loading line from dict: 100%|██████████| 30702/30702 [00:01<00:00, 18719.16it/s]


Done loading line from dict.           


Loading line from dict: 100%|██████████| 30738/30738 [00:01<00:00, 18554.92it/s]


Done loading line from dict.           


Create the knobs for wire current and wire distance to the beam

In [29]:
tw = line.twiss()
tw.rows['ip.*'][['x','px', 'y', 'py', 'betx', 'bety']]

Found suitable prebuilt kernel `default_only_xtrack`.


TwissTable: 9 rows, 7 cols
name                                x           px            y           py     betx     bety
ip3                      -2.91699e-07 -5.89171e-09  1.61233e-07  1.50322e-09  121.566   218.58
ip2                      -0.000999997  1.30096e-10  5.91855e-09  0.000199996  9.99985  10.0002
ip1                      -2.49133e-10  8.46817e-10 -6.18254e-09  -9.9588e-09 0.300001 0.299991
ip1.l1                   -2.49133e-10  8.46817e-10 -6.18254e-09  -9.9588e-09 0.300001 0.299991
ip8                      -0.000999999  3.86712e-10  2.98839e-09  0.000199993  1.99999  2.00004
ip7                      -1.29335e-08  1.21493e-10  1.39908e-08  1.16815e-09  120.814  149.433
ip6                      -1.02698e-07  8.92232e-10    1.686e-07 -5.68459e-10  189.335   175.47
ip5                       -2.5092e-10  1.24665e-09  4.95186e-10  2.32122e-08      0.3 0.300004
ip4                      -8.97831e-09 -1.81831e-11  1.83098e-07 -1.13735e-10  231.103  303.944

In [30]:
# IP 1
line.vars[f'i_wire_ip1.{BEAM}'] = 0.0 
line.vars[f'd_wire_ip1.{BEAM}'] = 0.01 

# IP 5
line.vars[f'i_wire_ip5.{BEAM}'] = 0.0
line.vars[f'd_wire_ip5.{BEAM}'] = 0.01

Insert (unconfigured) wires on the line

In [31]:

side = 'r' if BEAM == 'b2' else 'l'
sign = 1 if BEAM == 'b2' else -1
l_name_wire = [f'bbwc.t.4{side}1', f'bbwc.b.4{side}1', f'bbwc.e.4{side}5', f'bbwc.i.4{side}5']
l_name_tct = [f'tctpv.4{side}1', f'tctpv.4{side}1', f'tctph.4{side}5', f'tctph.4{side}5']
l_h_dist = sign * np.array([0., 0., 1., -1.])
l_v_dist = 1 * np.array([1., -1., 0., 0.])

# Tw to get the position of the tct, but need to discard tracker afterwards to unfreeze the line
tw = line.twiss()
l_s_tct = [((tw.rows[f'{name_tct}.{BEAM}_entry'].s + tw.rows[f'{name_tct}.{BEAM}_exit'].s)/2)[0] for name_tct in l_name_tct]
line.discard_tracker()
for name_wire, name_tct, h_dist, v_dist, s_tct in zip(l_name_wire, l_name_tct, l_h_dist, l_v_dist, l_s_tct):
    line.insert_element(name=f'{name_wire}.{BEAM}',
                        element=xt.Wire(
                            L_phy=1, 
                            L_int=2,
                            current= 0.0,
                            xma=h_dist, 
                            yma= v_dist # very far from the beam
                            ),
                        at_s = s_tct
                        )


In [32]:
tw = line.twiss()
tw.rows['ip.*'][['x','px', 'y', 'py', 'betx', 'bety']]

Found suitable prebuilt kernel `default_only_xtrack`.


TwissTable: 9 rows, 7 cols
name                                x           px            y           py     betx     bety
ip3                      -2.91699e-07 -5.89171e-09  1.61233e-07  1.50322e-09  121.566   218.58
ip2                      -0.000999997  1.30096e-10  5.91855e-09  0.000199996  9.99985  10.0002
ip1                      -2.49133e-10  8.46817e-10 -6.18254e-09  -9.9588e-09 0.300001 0.299991
ip1.l1                   -2.49133e-10  8.46817e-10 -6.18254e-09  -9.9588e-09 0.300001 0.299991
ip8                      -0.000999999  3.86712e-10  2.98839e-09  0.000199993  1.99999  2.00004
ip7                      -1.29335e-08  1.21493e-10  1.39908e-08  1.16815e-09  120.814  149.433
ip6                      -1.02698e-07  8.92232e-10    1.686e-07 -5.68459e-10  189.335   175.47
ip5                       -2.5092e-10  1.24665e-09  4.95186e-10  2.32122e-08      0.3 0.300004
ip4                      -8.97831e-09 -1.81831e-11  1.83098e-07 -1.13735e-10  231.103  303.944

Get closed orbit position at the location of the wire

In [33]:
tw = line.twiss()
# Careful, tct are repeated so only take one out of two
x_tct_ip1, x_tct_ip5 = [((tw.rows[f'{name_tct}.{BEAM}_entry'].x + tw.rows[f'{name_tct}.{BEAM}_exit'].x)/2)[0] for name_tct in l_name_tct[::2]]
y_tct_ip1, y_tct_ip5 = [((tw.rows[f'{name_tct}.{BEAM}_entry'].y + tw.rows[f'{name_tct}.{BEAM}_exit'].y)/2)[0] for name_tct in l_name_tct[::2]]



Create corresponding knob for closed orbit

In [34]:
for co_wire, co in zip([f'co_y_wire_ip1.{BEAM}', f'co_x_wire_ip1.{BEAM}', f'co_y_wire_ip5.{BEAM}', f'co_x_wire_ip5.{BEAM}'], [y_tct_ip1, x_tct_ip1, y_tct_ip5, x_tct_ip5]):
    line.vars[co_wire] = co


Create knob for current scaling, and wire distance scaling

In [35]:
for name_wire in l_name_wire:
    
    # Check IP
    if 'r1' in name_wire or 'l1' in name_wire:
        ip = 1
        plane = 'y'
    elif 'r5' in name_wire or 'l5' in name_wire:
        ip = 5
        plane = 'x'
    else:
        raise ValueError('Invalid wire name')
    
    # Check sign
    if '.t.' in name_wire:
        sign = 1
    elif '.b.' in name_wire:
        sign = -1
    elif '.e.' in name_wire:
        if BEAM == 'b2':
            sign = 1
        else:
            sign = -1
    elif '.i.' in name_wire:
        if BEAM == 'b2':
            sign = -1
        else:
            sign = 1
    else:
        raise ValueError('Invalid wire name')
    
    # Assign knob
    line.element_refs[f'{name_wire}.{BEAM}'].current = line.vars[f'i_wire_ip{ip}.{BEAM}']
    if plane == 'y':
        line.element_refs[f'{name_wire}.{BEAM}'].yma = sign*line.vars[f'd_wire_ip{ip}.{BEAM}'] + line.vars[f'co_y_wire_ip{ip}.{BEAM}']
    else:
        line.element_refs[f'{name_wire}.{BEAM}'].xma = sign*line.vars[f'd_wire_ip{ip}.{BEAM}'] + line.vars[f'co_x_wire_ip{ip}.{BEAM}']


In [36]:
tw = line.twiss()
print(tw.qx, tw.qy)
tw.rows['ip.*'][['x','px', 'y', 'py', 'betx', 'bety']]

62.31000002611538 60.32000000072882


TwissTable: 9 rows, 7 cols
name                                x           px            y           py     betx     bety
ip3                      -2.91699e-07 -5.89171e-09  1.61233e-07  1.50322e-09  121.566   218.58
ip2                      -0.000999997  1.30096e-10  5.91855e-09  0.000199996  9.99985  10.0002
ip1                      -2.49133e-10  8.46817e-10 -6.18254e-09  -9.9588e-09 0.300001 0.299991
ip1.l1                   -2.49133e-10  8.46817e-10 -6.18254e-09  -9.9588e-09 0.300001 0.299991
ip8                      -0.000999999  3.86712e-10  2.98839e-09  0.000199993  1.99999  2.00004
ip7                      -1.29335e-08  1.21493e-10  1.39908e-08  1.16815e-09  120.814  149.433
ip6                      -1.02698e-07  8.92232e-10    1.686e-07 -5.68459e-10  189.335   175.47
ip5                       -2.5092e-10  1.24665e-09  4.95186e-10  2.32122e-08      0.3 0.300004
ip4                      -8.97831e-09 -1.81831e-11  1.83098e-07 -1.13735e-10  231.103  303.944

Close separation and crossing in IP2 and IP8 and ensure that orbit is flat

In [37]:
for ip in [2,8]:
        collider.vars[f'on_x{ip}h'] = 0.0
        collider.vars[f'on_x{ip}v'] = 0.0
        collider.vars[f'on_sep{ip}h'] = 0.0
        collider.vars[f'on_sep{ip}v'] = 0.0

for ip in [1,2,5,8]:
        print(8*'*', f'IP{ip}', 8*'*')
        if ip in [2,8]:
                print(f'on_sep{ip}h:\t ', collider.vars[f'on_sep{ip}h']._get_value())
                print(f'on_sep{ip}v:\t ', collider.vars[f'on_sep{ip}v']._get_value())
        else:
                print(f'on_x{ip}:\t\t ', collider.vars[f'on_x{ip}']._get_value())
                print(f'on_sep{ip}:\t ', collider.vars[f'on_sep{ip}']._get_value())
        print(f'on_oh{ip}:\t\t ', collider.vars[f'on_oh{ip}']._get_value())
        print(f'on_ov{ip}:\t\t ', collider.vars[f'on_ov{ip}']._get_value())
        print(f'on_a{ip}:\t\t ', collider.vars[f'on_a{ip}']._get_value())

print(8*'*', 'others settings', 8*'*')
print('on_alice_normalized:\t', collider.vars['on_alice_normalized']._get_value())
print('on_lhcb_normalized:\t', collider.vars['on_lhcb_normalized']._get_value())
print('on_disp:\t\t', collider.vars['on_disp']._get_value())

******** IP1 ********
on_x1:		  0.0
on_sep1:	  0.0
on_oh1:		  0.0
on_ov1:		  0.0
on_a1:		  0.0
******** IP2 ********
on_sep2h:	  0.0
on_sep2v:	  0.0
on_oh2:		  0.0
on_ov2:		  0.0
on_a2:		  0.0
******** IP5 ********
on_x5:		  0.0
on_sep5:	  0.0
on_oh5:		  0.0
on_ov5:		  0.0
on_a5:		  0.0
******** IP8 ********
on_sep8h:	  0.0
on_sep8v:	  0.0
on_oh8:		  0.0
on_ov8:		  0.0
on_a8:		  0.0
******** others settings ********
on_alice_normalized:	 0.0
on_lhcb_normalized:	 0.0
on_disp:		 0.0


Load all knobs

In [38]:
#Lod knob for both IPs

with open(f'/afs/cern.ch/work/c/cdroin/private/example_DA_study_runIII_wire/master_study/master_jobs/knobs_wire/knob_dict_350A_8sigma@30cm_ip5_beta30_{BEAM}.json') as f:
    data_ip5 = json.load(f)

with open(f'/afs/cern.ch/work/c/cdroin/private/example_DA_study_runIII_wire/master_study/master_jobs/knobs_wire/knob_dict_350A_8sigma@30cm_ip1_beta30_{BEAM}.json') as f:
    data_ip1 = json.load(f)

Update wire distances

In [39]:
side = 'r' if BEAM == 'b2' else 'l'
line.vars[f'd_wire_ip1.{BEAM}'] = data_ip1['tct_opening_in_sigma'] * data_ip1[f'sigma_y_at_tctpv_4{side}1_{BEAM}'] + data_ip1['wire_retraction']
line.vars[f'd_wire_ip5.{BEAM}'] = data_ip5['tct_opening_in_sigma'] * data_ip5[f'sigma_x_at_tctph_4{side}5_{BEAM}'] + data_ip5['wire_retraction']

Assert initial k are correct in the knob

In [40]:
for k0 in data_ip1['k_0']:
    assert data_ip1['k_0'][k0] == line.vars[k0]._get_value()
    

Define list of k for the matching (setting them to 0 initially)

In [41]:
k_list_for_matching = [
    f"kq5.l1{BEAM}",
    f"kq5.r1{BEAM}",
    f"kq6.l1{BEAM}",
    f"kq6.r1{BEAM}",
    f"kq7.l1{BEAM}",
    f"kq7.r1{BEAM}",
    f"kq8.l1{BEAM}",
    f"kq8.r1{BEAM}",
    f"kq9.l1{BEAM}",
    f"kq9.r1{BEAM}",
    f"kq10.l1{BEAM}",
    f"kq10.r1{BEAM}",
    f"kqtl11.r1{BEAM}",
    f"kqt12.r1{BEAM}",
    f"kqt13.r1{BEAM}",
    f"kq4.l5{BEAM}",
    f"kq4.r5{BEAM}",
    f"kq5.l5{BEAM}",
    f"kq5.r5{BEAM}",
    f"kq6.l5{BEAM}",
    f"kq6.r5{BEAM}",
    f"kq7.l5{BEAM}",
    f"kq7.r5{BEAM}",
    f"kq8.l5{BEAM}",
    f"kq8.r5{BEAM}",
    f"kq9.l5{BEAM}",
    f"kq9.r5{BEAM}",
    f"kq10.l5{BEAM}",
    f"kq10.r5{BEAM}",
    f"kqtl11.r5{BEAM}",
    f"kqt12.r5{BEAM}",
    f"kqt13.r5{BEAM}",
]


Define/reset the delta_k, used to scale the knob with current

In [42]:
def reset_delta_k(k_list):
    for kk in k_list:
        collider.vars[f"{kk}_delta"] = 0.000000
reset_delta_k(k_list_for_matching)

Set the k

In [43]:
for k in k_list_for_matching:
        collider.vars[f'{k}_0'] = collider.vars[k]._get_value()
        collider.vars[f'{k}_delta'] = 0.000000
        if '.r1' in k or '.l1' in k:
                collider.vars[k] = collider.vars[f'{k}_0'] + collider.vars[f'{k}_delta']*collider.vars[f'i_wire_ip1.{BEAM}']/350
        elif '.r5' in k or '.l5' in k:
                collider.vars[k] = collider.vars[f'{k}_0'] + collider.vars[f'{k}_delta']*collider.vars[f'i_wire_ip5.{BEAM}']/350

Set the delta_k

In [44]:
for data in [data_ip1, data_ip5]:
    for delta_k in data['k_delta']:
        collider.vars[f'{delta_k}_delta'] = data['k_delta'][delta_k]

In [45]:
# line.vars[f'i_wire_ip1.{BEAM}'] = 0.
# line.vars[f'i_wire_ip5.{BEAM}'] = 0.
# tw_ref = line.twiss(method='4d')
# print(line.vars['i_wire_ip1.b2']._value)
# line.vars['i_wire_ip1.b2'] = data['i_wire_ip1.b2']
# line.vars['i_wire_ip5.b2'] = data['i_wire_ip5.b2']
# print(data['i_wire_ip5.b2'])
# print(data['i_wire_ip1.b2'])

# tw_new = line.twiss(method='4d')
# plt.plot(tw_ref['s'], (tw_new['betx']- tw_ref['betx'])/tw_ref['betx'], label='ref')
# plt.plot(tw_ref['s'], (tw_new['bety']- tw_ref['bety'])/tw_ref['bety'], label='ref')
# plt.show()

Set the current

In [46]:
def plot_beta():
    fig = go.Figure()

    # Get ref current
    line.vars[f'i_wire_ip1.{BEAM}'] = 0.
    line.vars[f'i_wire_ip5.{BEAM}'] = 0.
    tw_ref = line.twiss(method = '4d')
    tw_first = None
    # Add traces, one for each slider step
    l_steps = np.arange(350, -50, -50)
    for idx, step in enumerate(l_steps):
        line.vars[f'i_wire_ip1.{BEAM}'] = float(step)
        #line.vars[f'i_wire_ip5.{BEAM}'] = float(step)    
        tw = line.twiss(method = '4d')
        if idx == 0:
            tw_first = line.twiss(method = '4d')

        fig.add_trace(
            go.Scattergl(
                visible=False,
                line=dict(color="#00CED1", width=6),
                name="Betx",
                x=tw_ref['s'][::20],
                y=(tw['betx'][::20] - tw_ref['betx'][::20]) / tw_ref['betx'][::20],
            )
        )
        fig.add_trace(
            go.Scattergl(
                visible=False,
                line=dict(color="orange", width=6),
                name="Bety",
                x=tw_ref['s'][::20],
                y=(tw['bety'][::20] - tw_ref['bety'][::20]) / tw_ref['bety'][::20],
            )
        )

    # Make 0th trace visible
    fig.data[0].visible = True
    fig.data[1].visible = True


    # Create and add slider
    steps = []
    for i in range(0,len(fig.data),2):
        step = dict(
            method="update",
            args=[{"visible": [False] * len(fig.data)},],  # layout attribute
        label=str(l_steps[i//2]))
        step["args"][0]["visible"][i] = True
        step["args"][0]["visible"][i+1] = True
        steps.append(step)

    sliders = [dict(
        active=0,
        currentvalue={"prefix": "Wire current (A): "},
        pad={"t": 50},
        steps=steps,
    )]

    fig.update_layout(
        sliders=sliders,
        yaxis=dict(range=[-0.1, 0.1], autorange=False)
    )
    fig.update_layout(template = 'plotly_white')
    # Label y axis
    fig.update_yaxes(title_text=r'Relative error on beta functions')
    return tw_ref, tw_first, fig



In [47]:
tw_ref, tw_first, fig = plot_beta()
fig.show()

Found suitable prebuilt kernel `only_xtrack_frozen_energy`.


In [48]:
# plt.plot(tw_ref['s'], tw_ref['x'])
# plt.plot(tw_ref['s'], tw_ref['y'])
# plt.show()

In [49]:
def plot_orbit():
    fig = go.Figure()

    # Get ref current
    line.vars[f'i_wire_ip1.{BEAM}'] = 0 #data_ip1[f'i_wire_ip1.{BEAM}']
    line.vars[f'i_wire_ip5.{BEAM}'] = 0 #data_ip5[f'i_wire_ip5.{BEAM}']
    tw_ref = line.twiss()

    # Add traces, one for each slider step
    l_steps = np.arange(350, -50, -50)
    for step in l_steps:
        line.vars[f'i_wire_ip1.{BEAM}'] = step
        line.vars[f'i_wire_ip5.{BEAM}'] = step
        tw = line.twiss()
        fig.add_trace(
            go.Scattergl(
                visible=False,
                line=dict(color="#00CED1", width=6),
                name="x",
                x=tw['s'][::20],
                y=np.log(abs(tw['x'][::20]- tw_ref['x'][::20])+1e-26)
                )
            )
        fig.add_trace(
            go.Scattergl(
                visible=False,
                line=dict(color="orange", width=6),
                name="y",
                x=tw['s'][::20],
                y=np.log(abs(tw['y'][::20]- tw_ref['y'][::20])+1e-26)
                )
            )
        
    # Make 0th trace visible
    fig.data[0].visible = True
    fig.data[1].visible = True

    # Create and add slider
    steps = []
    for i in range(0,len(fig.data),2):
        step = dict(
            method="update",
            args=[{"visible": [False] * len(fig.data)},],  # layout attribute
        label=str(l_steps[i//2]))
        step["args"][0]["visible"][i] = True
        step["args"][0]["visible"][i+1] = True
        steps.append(step)

    sliders = [dict(
        active=0,
        currentvalue={"prefix": "Wire current (A): "},
        pad={"t": 50},
        steps=steps,
    )]

    fig.update_layout(
        sliders=sliders,
        yaxis=dict(range=[-28, -8], autorange=False)
    )
    fig.update_layout(template = 'plotly_white')

    # Label y axis
    fig.update_yaxes(title_text=r'Log(Absolute error on closed-orbit)')
    
    return fig




In [51]:
fig = plot_orbit()
fig.show()